In [2]:
# add libraries
import requests
import json
import pandas as pd
import os
from pprint import pprint
import time

# Data Acquisition

First have to get PUUID (unique id for players) that is required to search through their matches.

To get PUUID, use LEAGUE-V4 to get a list of players to search up using SUMMONER-V4 to get PUUID. After acquiring PUUID for players, use that PUUID to query in MATCH-V5 to get recent matches. Using those matches, get the timelines for each match at 10 minute mark.

In [3]:
# acquire data from different API endpoints
# League-V4

queue = 'RANKED_SOLO_5x5'
tier = 'DIAMOND'
division = 'I'

# pages of players
# iterate through pages 1-5 to get ~1000 players to use as sample data for now
params = {
    "page": 1
}

url = 'https://na1.api.riotgames.com/lol/'
league_url = f'{url}league/v4/entries/{queue}/{tier}/{division}'

headers = {}
headers["X-Riot-Token"] = 'RGAPI-a43d7510-dfa5-4bf9-bb2b-fd84651d468b'

In [4]:
league_data = []
for i in range(5):
    params["page"] = i + 1
    res = requests.get(url = league_url, params = params, headers = headers)
    league_data.append(res.json())

In [5]:
pprint(league_data)

[[{'freshBlood': False,
   'hotStreak': False,
   'inactive': False,
   'leagueId': 'a8a62145-cbe2-46ef-969e-dd54e34cb0d0',
   'leaguePoints': 0,
   'losses': 850,
   'queueType': 'RANKED_SOLO_5x5',
   'rank': 'I',
   'summonerId': 'OY75KH9QbWHY3khIgtPZ13Lj08JpC9vZVd4aALT5WbCuEknk',
   'summonerName': 'zendeptrai98',
   'tier': 'DIAMOND',
   'veteran': False,
   'wins': 868},
  {'freshBlood': False,
   'hotStreak': False,
   'inactive': False,
   'leagueId': '6f562d61-c963-4ff0-895e-9a76c7e51138',
   'leaguePoints': 24,
   'losses': 33,
   'queueType': 'RANKED_SOLO_5x5',
   'rank': 'I',
   'summonerId': 'cQlO5u1f9lPhawcidmQ5wdd2zBTRlGvpIEexTh6DmNNzESqi',
   'summonerName': 'zgren shi ji lao',
   'tier': 'DIAMOND',
   'veteran': False,
   'wins': 53},
  {'freshBlood': False,
   'hotStreak': False,
   'inactive': False,
   'leagueId': 'b7f20e06-daf8-4f9d-b88c-9c0e772b1cb3',
   'leaguePoints': 39,
   'losses': 315,
   'queueType': 'RANKED_SOLO_5x5',
   'rank': 'I',
   'summonerId': '1bQ06

In [6]:
# get the summonerId's to search up
summoner_ids = []
for page in league_data:
    for entry in page:
        summoner_ids.append(entry.get('summonerId'))

In [7]:
len(summoner_ids)

1025

In [8]:
# get the PUUID and save them to a pd dataframe
# work with the first 100 puuids for now
# SUMMONER-V4

summoner_data = []

for id in summoner_ids[0:100]:
    summoner_url = f'{url}summoner/v4/summoners/{id}'
    res = requests.get(url = summoner_url, headers = headers)
    summoner_data.append(res.json())
    time.sleep(1)

In [9]:
pprint(summoner_data[0:5])

[{'accountId': '-imBqXJV9jnRcCGZIN5smoGKhA_nq13n3_jJLj2UFhG4WKU0v7smPMdh',
  'id': 'OY75KH9QbWHY3khIgtPZ13Lj08JpC9vZVd4aALT5WbCuEknk',
  'name': 'zendeptrai98',
  'profileIconId': 4651,
  'puuid': 'tVK31ohih_XSJLQ1d-fsj_D9GiNzjFAQgLb2WCfOiqbMrfpWCC-Fke8cVxOhjw6mhIRmSXBIbsjCDA',
  'revisionDate': 1669088605000,
  'summonerLevel': 436},
 {'accountId': 'RqCJF-y-fISEAo4i7E-J1aAs2AudCUkZW-fHCeDbA-Izi99mFPIh-5oa',
  'id': 'cQlO5u1f9lPhawcidmQ5wdd2zBTRlGvpIEexTh6DmNNzESqi',
  'name': 'zgren shi ji lao',
  'profileIconId': 2076,
  'puuid': 'NsQ3lRIhO9C5l8q4-gS8KbxaWGVbW9TSJ3yIyBPyPC4geLLriMF3hGDhVtIDZ6YVMvts9u5N6RvtNQ',
  'revisionDate': 1667799022000,
  'summonerLevel': 291},
 {'accountId': 'N1pjHONJwEZhoDQztm0--_YDXm7pssJ8USEZjAEudMviODDLXbydZhod',
  'id': '1bQ06mF0XHYbapHt9QsIbxSR7-NZUVBCz-aCZFXUoFcQFiIZ',
  'name': 'bombtruck457',
  'profileIconId': 5030,
  'puuid': 'imwKAYy65ucD9IgEO-bbogibzDZ4VMBHvfAge6LsiQyKMrj3OVOyUM6CJiRfHbVHER4AgCz1h4WVHA',
  'revisionDate': 1669208937000,
  'summone

In [10]:
puuids = []
for summoner in summoner_data:
    puuids.append(summoner.get('puuid'))

In [11]:
len(puuids)

99

In [16]:
puuids[0]

'tVK31ohih_XSJLQ1d-fsj_D9GiNzjFAQgLb2WCfOiqbMrfpWCC-Fke8cVxOhjw6mhIRmSXBIbsjCDA'

In [31]:
# get the 10 most recent games for puuid
# store into set so no duplicate games are used
last_10_games = []

params = {
    "queue": 420,
    "start": -1,
    "count": 10
}

for puuid in puuids[0:5]:
    last_10_url = f"https://americas.api.riotgames.com/lol/match/v5/matches/by-puuid/{puuid}/ids"
    res = requests.get(url = last_10_url, params = params, headers = headers)
    for match_id in res.json():
        last_10_games.append(match_id)
    time.sleep(1)

In [32]:
len(last_10_games)

45

In [33]:
# get info from each match at 10 minute mark
match_id = last_10_games[0]

match_url = f"https://americas.api.riotgames.com/lol/match/v5/matches/{match_id}/timeline"
res = requests.get(url = match_url, headers = headers)

In [34]:
match = res.json()

In [38]:
pprint(match)

{'info': {'frameInterval': 60000,
          'frames': [{'events': [{'realTimestamp': 1669377090476,
                                  'timestamp': 0,
                                  'type': 'PAUSE_END'}],
                      'participantFrames': {'1': {'championStats': {'abilityHaste': 0,
                                                                    'abilityPower': 0,
                                                                    'armor': 35,
                                                                    'armorPen': 0,
                                                                    'armorPenPercent': 0,
                                                                    'attackDamage': 25,
                                                                    'attackSpeed': 100,
                                                                    'bonusArmorPenPercent': 0,
                                                                    'bonusMagicPenPercent': 0,

# Feature Engineering

participants 1-5 are blue side

6-10 are red side

WARDS:

WARD_KILL

WARD_PLACED

ITEM_DESTROYED: 2055 (control ward)

KILLS:

CHAMIPON_KILLS

OBJECTIVES:

TURRET_PLATE_DESTROYED

BUILDING_KILL

ELITE_MONSTER_KILL

Each frame is 60 seconds of gameplay.
So for each frame need to record the events by parsing through the request
like wards placed
count total kills from each frame as well

In [53]:
print(len(match['info']['frames']))

37


In [78]:
pprint(match['info']['frames'])

[{'events': [{'realTimestamp': 1669377090476,
              'timestamp': 0,
              'type': 'PAUSE_END'}],
  'participantFrames': {'1': {'championStats': {'abilityHaste': 0,
                                                'abilityPower': 0,
                                                'armor': 35,
                                                'armorPen': 0,
                                                'armorPenPercent': 0,
                                                'attackDamage': 25,
                                                'attackSpeed': 100,
                                                'bonusArmorPenPercent': 0,
                                                'bonusMagicPenPercent': 0,
                                                'ccReduction': 0,
                                                'cooldownReduction': 0,
                                                'health': 660,
                                                'healthMax': 660,
      

In [79]:
# make a dataframe with matchid as index and features as columns